In [3]:
import json
import numpy as np
import hnswlib
import networkx as nx
from collections import defaultdict

## Reading Embeddings and creating Indexer for NN search

In [34]:
IDList = []                                # List of paper IDs
NNList = []                                # List of list, NNList[i]: NNs to paper whose id is IDList[i]
embeddings = []                            # Embeddings read from the input file

with open('dblpAbstractFTEmbeddings.json', 'r') as file:
    for line in file:
        data = json.loads(line)
        paperID = data['id']
        embedding = data['embedding']
        IDList.append(paperID)
        embeddings.append(embedding)

In [35]:
numElements = len(IDList)
dimension = len(embeddings[0])
embeddings = np.asarray(embeddings)
data_labels = np.arange(numElements)

In [36]:
p = hnswlib.Index(space = 'cosine', dim = dimension) # possible options are l2, cosine or ip

# Initing index - the maximum number of elements should be known beforehand
p.init_index(max_elements = numElements, ef_construction = 200, M = 20)

# Element insertion (can be called several times):
p.add_items(embeddings, data_labels)

# Controlling the recall by setting ef:
p.set_ef(50) # ef should always be > k

# Query dataset, k - number of closest elements (returns 2 numpy arrays)
labels, _ = p.knn_query(embeddings, k = 5)

In [37]:
index_path='fastTexthnswlib.bin'
print("Saving index to '%s'" % index_path)
p.save_index("fastTexthnswlib.bin")
del p

Saving index to 'fastTexthnswlib.bin'


In [43]:

label = [paperId for paperId in labels[3] if paperId != 3]

In [47]:
[i for i in range(5)]

[0, 1, 2, 3, 4]

## Examples of NN obtained using the Text Embeddings

In [45]:
titles = []
with open('dblp_AIpapers_v11.json', 'r') as file:
    for line in file:
        data = json.loads(line)
        titles.append(data['title'])

In [52]:
count = 5
for i in range(count):
    print('Paper: ', titles[i])
    print('Nearest Papers: ', [titles[ind] for ind in labels[i] if ind != i])
    print('\n')

Paper:  Gait based human identity recognition from multi-view surveillance videos
Nearest Papers:  ['Generation of Temporally Consistent Multiple Virtual Camera Views from Stereoscopic Image Sequences', 'Recycled paper visual indexing for quality control', 'Face recognition by thermal video using 3D information and vesselness features', 'Touchless Multiview Fingerprint Acquisition and Mosaicking', 'Object Search and Localization for an Indoor Mobile Robot']


Paper:  The GAME Algorithm Applied to Complex Fractionated Atrial Electrograms Data Set
Nearest Papers:  ['Expert systems for time-varying biomedical signals using eigenvector methods', 'Multichannel lung sound analysis for asthma detection', 'Evidence-Based Combination of Weighted Classifiers Approach for Epileptic Seizure Detection using EEG Signals', 'A multi-modal classifier for heart sound recordings']


Paper:  Principle-Based Parsing and Type Inference.
Nearest Papers:  ['Context-Modeled Wavelet Difference Reduction Coding 

## Building Adjacency List for Node Embeddings

### Creating Citation Adjacency List

In [77]:
adjList = defaultdict(set)                          # Convert set to list later for node2vec, set: to handle duplicates
with open('dblp_AIpapers_v11.json', 'r') as file:
    for line in file:
        data = json.loads(line)
        paperID = data['id']
        references = data.get('references', [])
        for referencedPaper in references:
            adjList[paperID].add(referencedPaper)
            adjList[referencedPaper].add(paperID)

### Augmenting Adj List with FastText NNs

In [78]:
nnToKeep = 3
id = 0
for label in labels:
    paperID = IDList[id]
    label = [IDList[index] for index in label if index != id]
    if (len(label) > nnToKeep):
        del label[nnToKeep:]
    for referencedPaper in label:
        adjList[paperID].add(referencedPaper)
        adjList[referencedPaper].add(paperID)
    id += 1

### Creating NetworkX Graph and reporting graph statistics

In [79]:
adjList = {key: list(values) for key, values in adjList.items()}
G = nx.from_dict_of_lists(adjList)

nnodes = G.number_of_nodes()
avgDegree = sum(d for n, d in G.degree()) / float(nnodes)
print('Number of nodes: ', nnodes, '. Number of edges: ', G.number_of_edges(), '. Avg Degree: ', avgDegree)

Number of nodes:  1305095 . Number of edges:  14241314 . Avg Degree:  21.82417984897651


## Node2Vec Embeddings

In [80]:
from node2vec import Node2Vec
node2vec = Node2Vec(G, walk_length = 7, workers = 6)
model = node2vec.fit()              # returns a gensim wv model



Computing transition probabilities:   0%|          | 0/1305095 [00:00<?, ?it/s]

Computing transition probabilities:   0%|          | 3/1305095 [00:00<13:14:50, 27.37it/s]

Computing transition probabilities:   0%|          | 4/1305095 [00:00<30:34:26, 11.86it/s]

Computing transition probabilities:   0%|          | 6/1305095 [00:00<29:09:21, 12.43it/s]

Computing transition probabilities:   0%|          | 8/1305095 [00:01<67:13:11,  5.39it/s]

Computing transition probabilities:   0%|          | 12/1305095 [00:03<101:33:21,  3.57it/s]

Computing transition probabilities:   0%|          | 14/1305095 [00:03<92:30:17,  3.92it/s] 

Computing transition probabilities:   0%|          | 16/1305095 [00:05<174:59:21,  2.07it/s]

Computing transition probabilities:   0%|          | 22/1305095 [00:05<124:29:46,  2.91it/s]

Computing transition probabilities:   0%|          | 26/1305095 [00:08<148:58:55,  2.43it/s]

Computing transition probabilities:   0%|          | 29/1305095 [00:10<188:14:5

Computing transition probabilities:   0%|          | 203/1305095 [01:14<97:48:41,  3.71it/s] 

Computing transition probabilities:   0%|          | 206/1305095 [01:14<73:48:19,  4.91it/s]

Computing transition probabilities:   0%|          | 208/1305095 [01:14<59:39:40,  6.08it/s]

Computing transition probabilities:   0%|          | 210/1305095 [01:16<136:14:34,  2.66it/s]

Computing transition probabilities:   0%|          | 213/1305095 [01:16<100:06:28,  3.62it/s]

Computing transition probabilities:   0%|          | 215/1305095 [01:16<76:55:30,  4.71it/s] 

Computing transition probabilities:   0%|          | 219/1305095 [01:16<59:51:35,  6.06it/s]

Computing transition probabilities:   0%|          | 223/1305095 [01:16<47:30:25,  7.63it/s]

Computing transition probabilities:   0%|          | 226/1305095 [01:17<39:13:51,  9.24it/s]

Computing transition probabilities:   0%|          | 228/1305095 [01:17<36:47:16,  9.85it/s]

Computing transition probabilities:   0%|          | 230

Computing transition probabilities:   0%|          | 388/1305095 [02:07<62:26:07,  5.80it/s]

Computing transition probabilities:   0%|          | 391/1305095 [02:09<115:10:41,  3.15it/s]

Computing transition probabilities:   0%|          | 396/1305095 [02:09<82:50:40,  4.37it/s] 

Computing transition probabilities:   0%|          | 399/1305095 [02:09<69:04:18,  5.25it/s]

Computing transition probabilities:   0%|          | 401/1305095 [02:10<70:50:31,  5.12it/s]

Computing transition probabilities:   0%|          | 403/1305095 [02:11<92:27:01,  3.92it/s]

Computing transition probabilities:   0%|          | 405/1305095 [02:15<285:33:52,  1.27it/s]

Computing transition probabilities:   0%|          | 406/1305095 [02:15<214:59:04,  1.69it/s]

Computing transition probabilities:   0%|          | 407/1305095 [02:15<170:48:15,  2.12it/s]

Computing transition probabilities:   0%|          | 413/1305095 [02:15<122:10:54,  2.97it/s]

Computing transition probabilities:   0%|          | 4

Computing transition probabilities:   0%|          | 607/1305095 [02:55<40:33:43,  8.93it/s]

Computing transition probabilities:   0%|          | 612/1305095 [02:56<31:48:10, 11.39it/s]

Computing transition probabilities:   0%|          | 616/1305095 [02:58<94:44:31,  3.82it/s]

Computing transition probabilities:   0%|          | 619/1305095 [02:58<69:56:36,  5.18it/s]

Computing transition probabilities:   0%|          | 625/1305095 [02:58<50:57:02,  7.11it/s]

Computing transition probabilities:   0%|          | 634/1305095 [03:00<51:57:18,  6.97it/s]

Computing transition probabilities:   0%|          | 637/1305095 [03:00<44:22:07,  8.17it/s]

Computing transition probabilities:   0%|          | 642/1305095 [03:00<33:18:02, 10.88it/s]

Computing transition probabilities:   0%|          | 645/1305095 [03:02<106:38:57,  3.40it/s]

Computing transition probabilities:   0%|          | 649/1305095 [03:04<127:08:49,  2.85it/s]

Computing transition probabilities:   0%|          | 651/1

Computing transition probabilities:   0%|          | 866/1305095 [03:51<60:02:47,  6.03it/s]

Computing transition probabilities:   0%|          | 868/1305095 [03:53<147:46:36,  2.45it/s]

Computing transition probabilities:   0%|          | 870/1305095 [03:54<126:57:18,  2.85it/s]

Computing transition probabilities:   0%|          | 871/1305095 [03:54<114:06:34,  3.17it/s]

Computing transition probabilities:   0%|          | 874/1305095 [03:54<85:44:45,  4.23it/s] 

Computing transition probabilities:   0%|          | 876/1305095 [03:54<79:34:39,  4.55it/s]

Computing transition probabilities:   0%|          | 877/1305095 [03:55<74:58:48,  4.83it/s]

Computing transition probabilities:   0%|          | 880/1305095 [03:55<57:57:38,  6.25it/s]

Computing transition probabilities:   0%|          | 882/1305095 [03:55<64:24:38,  5.62it/s]

Computing transition probabilities:   0%|          | 884/1305095 [03:55<56:27:03,  6.42it/s]

Computing transition probabilities:   0%|          | 886

...

Computing transition probabilities:  15%|█▍        | 189831/1305095 [6:48:58<31:25:58,  9.86it/s]

Computing transition probabilities:  15%|█▍        | 189838/1305095 [6:48:58<24:14:18, 12.78it/s]

Computing transition probabilities:  15%|█▍        | 189843/1305095 [6:48:59<20:03:12, 15.45it/s]

Computing transition probabilities:  15%|█▍        | 189859/1305095 [6:48:59<14:38:34, 21.16it/s]

Computing transition probabilities:  15%|█▍        | 189867/1305095 [6:49:03<54:16:06,  5.71it/s]

Computing transition probabilities:  15%|█▍        | 189873/1305095 [6:49:03<40:35:32,  7.63it/s]

Computing transition probabilities:  15%|█▍        | 189878/1305095 [6:49:03<39:05:58,  7.92it/s]

Computing transition probabilities:  15%|█▍        | 189882/1305095 [6:49:04<36:47:55,  8.42it/s]

Computing transition probabilities:  15%|█▍        | 189892/1305095 [6:49:04<26:42:24, 11.60it/s]

Computing transition probabilities:  15%|█▍        | 189897/1305095 [6:49:04<24:47:54, 12.49it/s]

Computing 

Computing transition probabilities:  15%|█▍        | 190348/1305095 [6:49:43<17:01:42, 18.18it/s]

Computing transition probabilities:  15%|█▍        | 190360/1305095 [6:49:43<12:43:01, 24.35it/s]

Computing transition probabilities:  15%|█▍        | 190367/1305095 [6:49:45<34:29:10,  8.98it/s]

Computing transition probabilities:  15%|█▍        | 190372/1305095 [6:49:45<26:46:07, 11.57it/s]

Computing transition probabilities:  15%|█▍        | 190377/1305095 [6:49:46<21:42:20, 14.27it/s]

Computing transition probabilities:  15%|█▍        | 190381/1305095 [6:49:47<59:14:50,  5.23it/s]

Computing transition probabilities:  15%|█▍        | 190386/1305095 [6:49:48<43:54:11,  7.05it/s]

Computing transition probabilities:  15%|█▍        | 190390/1305095 [6:49:51<118:15:34,  2.62it/s]

Computing transition probabilities:  15%|█▍        | 190399/1305095 [6:49:53<102:42:12,  3.01it/s]

Computing transition probabilities:  15%|█▍        | 190402/1305095 [6:49:53<75:20:43,  4.11it/s] 

Computi

Computing transition probabilities:  15%|█▍        | 190789/1305095 [6:50:34<7:25:00, 41.73it/s]

Computing transition probabilities:  15%|█▍        | 190796/1305095 [6:50:34<7:04:34, 43.74it/s]

Computing transition probabilities:  15%|█▍        | 190802/1305095 [6:50:36<37:28:34,  8.26it/s]

Computing transition probabilities:  15%|█▍        | 190807/1305095 [6:50:36<33:13:05,  9.32it/s]

Computing transition probabilities:  15%|█▍        | 190812/1305095 [6:50:37<25:48:26, 11.99it/s]

Computing transition probabilities:  15%|█▍        | 190818/1305095 [6:50:37<19:40:31, 15.73it/s]

Computing transition probabilities:  15%|█▍        | 190823/1305095 [6:50:37<16:12:39, 19.09it/s]

Computing transition probabilities:  15%|█▍        | 190834/1305095 [6:50:39<27:55:51, 11.08it/s]

Computing transition probabilities:  15%|█▍        | 190837/1305095 [6:50:43<136:14:39,  2.27it/s]

Computing transition probabilities:  15%|█▍        | 190840/1305095 [6:50:43<98:31:30,  3.14it/s] 

Computing 

Computing transition probabilities:  15%|█▍        | 191254/1305095 [6:51:26<39:48:56,  7.77it/s]

Computing transition probabilities:  15%|█▍        | 191259/1305095 [6:51:26<29:48:28, 10.38it/s]

Computing transition probabilities:  15%|█▍        | 191264/1305095 [6:51:28<58:51:00,  5.26it/s]

Computing transition probabilities:  15%|█▍        | 191270/1305095 [6:51:28<43:20:30,  7.14it/s]

Computing transition probabilities:  15%|█▍        | 191274/1305095 [6:51:28<33:41:41,  9.18it/s]

Computing transition probabilities:  15%|█▍        | 191278/1305095 [6:51:29<27:42:47, 11.16it/s]

Computing transition probabilities:  15%|█▍        | 191282/1305095 [6:51:31<68:16:18,  4.53it/s]

Computing transition probabilities:  15%|█▍        | 191286/1305095 [6:51:31<51:26:34,  6.01it/s]

Computing transition probabilities:  15%|█▍        | 191291/1305095 [6:51:31<39:30:11,  7.83it/s]

Computing transition probabilities:  15%|█▍        | 191294/1305095 [6:51:31<34:49:22,  8.88it/s]

Computing 

KeyboardInterrupt: 